In [2]:
# use the dev version of Oscar:
# using Pkg; Pkg.add("Oscar")
# Pkg.develop(path=raw"insert_here_your_path_to_Oscar.jl")

In [1]:
using Oscar
using LinearAlgebra

 -----    -----    -----      -      -----   
|     |  |     |  |     |    | |    |     |  
|     |  |        |         |   |   |     |  
|     |   -----   |        |     |  |-----   
|     |        |  |        |-----|  |   |    
|     |  |     |  |     |  |     |  |    |   
 -----    -----    -----   -     -  -     -  

...combining (and extending) ANTIC, GAP, Polymake and Singular
Version 0.8.2-DEV ... 
 ... which comes with absolutely no warranty whatsoever
Type: '?Oscar' for more information
(c) 2019-2022 by The Oscar Development Team


# Step by step algorithm 

We compute the radial function of intersection bodies step by step. We present the algorithm for the cube centered at the origin in dimension $d=3$.

In [2]:
P = cube(3)
d = Oscar.dim(P)
dim = Oscar.dim

dim (generic function with 35 methods)

Compute the associated zonotope $Z(P)$ which is the Minkowski sum of $[-v,v]$ for the vertices $v$ of $P$.

In [3]:
vert = collect(vertices(P))
Z = sum(convex_hull(transpose([-vert[i] vert[i]])) for i=1:length(vert))

A polyhedron in ambient dimension 3

Compute the normal fan $\Sigma$ of $Z(P)$.

In [4]:
Σ = normal_fan(Z)
Σ_cones = collect(maximal_cones(Σ))

14-element Vector{Cone{fmpq}}:
 A polyhedral cone in ambient dimension 3
 A polyhedral cone in ambient dimension 3
 A polyhedral cone in ambient dimension 3
 A polyhedral cone in ambient dimension 3
 A polyhedral cone in ambient dimension 3
 A polyhedral cone in ambient dimension 3
 A polyhedral cone in ambient dimension 3
 A polyhedral cone in ambient dimension 3
 A polyhedral cone in ambient dimension 3
 A polyhedral cone in ambient dimension 3
 A polyhedral cone in ambient dimension 3
 A polyhedral cone in ambient dimension 3
 A polyhedral cone in ambient dimension 3
 A polyhedral cone in ambient dimension 3

Construct a point called `u_sample` in the interior of the i-th maximal cone of $\Sigma$.

In [5]:
i = 1
u_sample = sum(rays(Σ_cones[i]))

3-element RayVector{fmpq}:
 0
 0
 -4

Contruct the hyperplane orthogonal to `u_sample`.

In [6]:
u_perp = Polyhedron(transpose([u_sample -u_sample]),[0; 0])

A polyhedron in ambient dimension 3

Step $1$: collect the facets of $P$ that intersect `u_perp` in dimension $d-2 = 1$.

In [7]:
P_facets = collect(faces(P,d-1))
relevantfacets = findall(ℓ -> dim(intersect(ℓ,u_perp))==d-2, P_facets)
intersecting_facets = P_facets[relevantfacets]

4-element Vector{Polyhedron{fmpq}}:
 A polyhedron in ambient dimension 3
 A polyhedron in ambient dimension 3
 A polyhedron in ambient dimension 3
 A polyhedron in ambient dimension 3

Step $2$: in the case $d=3$ triangulations are not necessary, so we skip this step.

In Step $5$ we will need the edges $e$ of $P$ such that $\text{dim}(e\cap u^{\perp})=0$. We collect them here.

In [8]:
edges = Polymake.to_one_based_indexing(Polymake.polytope.faces_of_dim(P.pm_polytope,1))
V = vertices(P)
good_edges = []
for edge in edges
    v = Vector{Int}(edge)
    first = transpose(Vector(u_sample)) * Vector(V[v[1]])
    last = transpose(Vector(u_sample)) * Vector(V[v[2]])
    if first * last < 0
        push!(good_edges, v)
    end
end
println(good_edges)

Any[[1, 5], [3, 7], [2, 6], [4, 8]]


In [9]:
good_facet_edges = []
for i in 1:Polymake.nrows(P.pm_polytope.VERTICES_IN_FACETS)
    facet = Polymake.row(P.pm_polytope.VERTICES_IN_FACETS,i)
    intersecting_edges = []
    for edge in good_edges
        test = length(intersect(Set(edge),Set(facet)))
        if test == 2
            push!(intersecting_edges, edge)
        end
    end
    if length(intersecting_edges) >= 2
        push!(good_facet_edges, intersecting_edges)
    end
end
print(good_facet_edges)

Any[Any[[1, 5], [3, 7]], Any[[2, 6], [4, 8]], Any[[1, 5], [2, 6]], Any[[3, 7], [4, 8]]]

Step $4-6$: collect the vertices of $Q$ in the form $\frac{b⋅x}{(b-a)⋅x}(a - b)+b$. For every edge of Step $5$ construct the associated matrix $M$, whose last row is the vector $(x_1,\ldots ,x_d)$. Compute and store its determinant.

In [10]:
R, (x1, x2, x3) = PolynomialRing(QQ, ["x1", "x2", "x3"]; ordering=:deglex)
S = FractionField(R) 

Fraction field of Multivariate Polynomial Ring in x1, x2, x3 over Rational Field

In [11]:
x = S[x1 x2 x3]

[x1   x2   x3]

In [12]:
vert = [[[V[e[1]],V[e[2]]] for e in edge_list] for edge_list in good_facet_edges]
vert = [[[[S.(j) for j ∈ entries] for entries ∈ v] for v ∈ vv] for vv ∈ vert]

4-element Vector{Vector{Vector{Vector{AbstractAlgebra.Generic.Frac{fmpq_mpoly}}}}}:
 [[[-1, -1, -1], [-1, -1, 1]], [[-1, 1, -1], [-1, 1, 1]]]
 [[[1, -1, -1], [1, -1, 1]], [[1, 1, -1], [1, 1, 1]]]
 [[[-1, -1, -1], [-1, -1, 1]], [[1, -1, -1], [1, -1, 1]]]
 [[[-1, 1, -1], [-1, 1, 1]], [[1, 1, -1], [1, 1, 1]]]

In [13]:
Q_vertices = [[((x⋅v[2]) //(x⋅v[2] - x⋅v[1])).*(v[1]-v[2]) + v[2]  for v ∈ vv] for vv ∈ vert]

4-element Vector{Vector{Vector{AbstractAlgebra.Generic.Frac{fmpq_mpoly}}}}:
 [[-1, -1, (x1 + x2)//x3], [-1, 1, (x1 - x2)//x3]]
 [[1, -1, (-x1 + x2)//x3], [1, 1, (-x1 - x2)//x3]]
 [[-1, -1, (x1 + x2)//x3], [1, -1, (-x1 + x2)//x3]]
 [[-1, 1, (x1 - x2)//x3], [1, 1, (-x1 - x2)//x3]]

In [14]:
determinants = []
for simplex ∈ Q_vertices
    M = S[simplex[1][1] simplex[1][2] simplex[1][3]; simplex[2][1] simplex[2][2] simplex[2][3]; x1 x2 x3]
    det_M = det(M)
    if det != 0
        sgn = sign(lc(numerator(det_M)))*sign(lc(denominator(det_M)))
    end
    push!(determinants,[sgn,det_M])
end
determinants

4-element Vector{Any}:
 FracElem[-1, (-2*x1^2 - 2*x2^2 - 2*x3^2)//x3]
 FracElem[1, (2*x1^2 + 2*x2^2 + 2*x3^2)//x3]
 FracElem[1, (2*x1^2 + 2*x2^2 + 2*x3^2)//x3]
 FracElem[-1, (-2*x1^2 - 2*x2^2 - 2*x3^2)//x3]

Step $13$: sum all the determinants and divide by the `correcting_factor`.

In [15]:
correcting_factor = 1//(factorial(d-1)*(x1^2+x2^2+x3^2))
rho = correcting_factor*sum(sng*det for (sng,det) ∈ determinants)


4//x3

# Complete functions

In [16]:
using Oscar
using LinearAlgebra

In [17]:
P = cube(3)
d = Oscar.dim(P)
dim = Oscar.dim

dim (generic function with 35 methods)

The following functions compute the intersection body of $3$-dimensional convex bodies, with the origin in the interior.

In [18]:
function fan_chambers(poly)
    vert = collect(vertices(P))
    Z = sum(convex_hull(transpose([-vert[i] vert[i]])) for i=1:length(vert))
    Σ = normal_fan(Z)
    Σ_cones = collect(maximal_cones(Σ))
    
    return Σ_cones
end

fan_chambers (generic function with 1 method)

In [19]:
function radial_function(poly)
    P = poly
    d = dim(P)
    Fan = fan_chambers(P)
    edges = Polymake.to_one_based_indexing(Polymake.polytope.faces_of_dim(P.pm_polytope,1))
    V = vertices(P)
    origin = zeros(d+1)
    res = []
    R, (x1, x2, x3) = PolynomialRing(QQ, ["x1", "x2", "x3"]; ordering=:deglex)
    S = FractionField(R)
    x = S[x1 x2 x3]
    
    for Σ_cones ∈ Fan
        u_sample = sum(rays(Σ_cones))
        u_perp = Polyhedron(transpose([u_sample -u_sample]),[0; 0])
        
        if dim(intersect(P,u_perp))==d-1
            good_edges = []
             for edge in edges
                v = Vector{Int}(edge)
                first = transpose(Vector(u_sample)) * Vector(V[v[1]])
                last = transpose(Vector(u_sample)) * Vector(V[v[2]])
                if first * last < 0
                    push!(good_edges, v)
                end
            end
            good_facet_edges = []
            for i in 1:Polymake.nrows(P.pm_polytope.VERTICES_IN_FACETS)
                facet = Polymake.row(P.pm_polytope.VERTICES_IN_FACETS,i)
                intersecting_edges = []
                for edge in good_edges
                    test = length(intersect(Set(edge),Set(facet)))
                    if test == 2
                        push!(intersecting_edges, edge)
                    end
                end
                if length(intersecting_edges) >= 2
                    push!(good_facet_edges, intersecting_edges)
                end
            end
            
            vert = [[[V[e[1]],V[e[2]]] for e in edge_list] for edge_list in good_facet_edges]
            vert = [[[[S.(j) for j ∈ entries] for entries ∈ v] for v ∈ vv] for vv ∈ vert]
            Q_vertices = [[((x⋅v[2]) //(x⋅v[2] - x⋅v[1])).*(v[1]-v[2]) + v[2]  for v ∈ vv] for vv ∈ vert]
            
            determinants = []
            for simplex ∈ Q_vertices
                M = S[simplex[1][1] simplex[1][2] simplex[1][3]; simplex[2][1] simplex[2][2] simplex[2][3]; x1 x2 x3]
                det_M = det(M)
                if det != 0
                    sgn = sign(lc(numerator(det_M)))*sign(lc(denominator(det_M)))
                end
                push!(determinants,[sgn,det_M])
            end
            
            correcting_factor = 1//(factorial(d-1)*(x1^2+x2^2+x3^2))
            rho = correcting_factor*sum(sng*det for (sng,det) ∈ determinants)

            push!(res, [rho, Σ_cones])
        else
            push!(res, [0, Σ_cones])
        end
    end
    return res
end
    

radial_function (generic function with 1 method)

In [21]:
@time r = radial_function(P)

  0.619077 seconds (377.27 k allocations: 10.605 MiB, 8.50% gc time)


14-element Vector{Any}:
 Any[4//x3, A polyhedral cone in ambient dimension 3]
 Any[(x1^2 - x2^2 + 2*x2*x3 - x3^2)//(x1*x2*x3), A polyhedral cone in ambient dimension 3]
 Any[(x1^2 + 2*x1*x2 + 2*x1*x3 + x2^2 - 2*x2*x3 + x3^2)//(x1*x2*x3), A polyhedral cone in ambient dimension 3]
 Any[4//x2, A polyhedral cone in ambient dimension 3]
 Any[(x1^2 + 2*x1*x2 + x2^2 - x3^2)//(x1*x2*x3), A polyhedral cone in ambient dimension 3]
 Any[4//x1, A polyhedral cone in ambient dimension 3]
 Any[(x1^2 + 2*x1*x3 - x2^2 + x3^2)//(x1*x2*x3), A polyhedral cone in ambient dimension 3]
 Any[(x1^2 + 2*x1*x3 - x2^2 + x3^2)//(x1*x2*x3), A polyhedral cone in ambient dimension 3]
 Any[4//x1, A polyhedral cone in ambient dimension 3]
 Any[(x1^2 + 2*x1*x2 + x2^2 - x3^2)//(x1*x2*x3), A polyhedral cone in ambient dimension 3]
 Any[4//x2, A polyhedral cone in ambient dimension 3]
 Any[(x1^2 + 2*x1*x2 + 2*x1*x3 + x2^2 - 2*x2*x3 + x3^2)//(x1*x2*x3), A polyhedral cone in ambient dimension 3]
 Any[(x1^2 - x2^2 + 2*x2*x3 -